# CHATBOTS - Using Natural Language Processing and Tensorflow

In [5]:
#Used in Tensorflow Model
import numpy as np
import tensorflow.compat.v1 as tf
tf.disable_v2_behavior()
import tflearn
import random

#Usde to for Contextualisation and Other NLP Tasks.
import nltk
from nltk.stem.lancaster import LancasterStemmer
stemmer = LancasterStemmer()

#Other
import json
import pickle
import warnings
warnings.filterwarnings("ignore")




Instructions for updating:
non-resource variables are not supported in the long term
curses is not supported on this machine (please install/reinstall curses for an optimal experience)



In [6]:
print("Processing the Intents.....")
with open('intents.json') as json_data:
    intents = json.load(json_data)



Processing the Intents.....


In [7]:
words = []
classes = []
documents = []
ignore_words = ['?']
print("Looping through the Intents to Convert them to words, classes, documents and ignore_words.......")
for intent in intents['intents']:
    for pattern in intent['patterns']:
        # tokenize each word in the sentence
        w = nltk.word_tokenize(pattern)
        # add to our words list
        words.extend(w)
        # add to documents in our corpus
        documents.append((w, intent['tag']))
        # add to our classes list
        if intent['tag'] not in classes:
            classes.append(intent['tag'])


Looping through the Intents to Convert them to words, classes, documents and ignore_words.......


In [8]:
print("Stemming, Lowering and Removing Duplicates.......")
words = [stemmer.stem(w.lower()) for w in words if w not in ignore_words]
words = sorted(list(set(words)))

# remove duplicates
classes = sorted(list(set(classes)))

print (len(documents), "documents")
print (len(classes), "classes", classes)
print (len(words), "unique stemmed words", words)

Stemming, Lowering and Removing Duplicates.......
98 documents
30 classes ['application_dates', 'ba', 'baallb', 'bba', 'bdesign', 'blu_embers_timings', 'bsc', 'btech', 'cafes', 'cost_of_study', 'courses', 'cup_of_joe_timings', 'doctors', 'eligibility_criteria', 'emergency', 'exchange_program', 'faculty', 'goodbye', 'greeting', 'hours', 'mba', 'meal_menu', 'meal_timings', 'new_embers_timings', 'online_payments', 'other_requirements', 'phd', 'restaurants', 'rise_timings', 'thanks']
125 unique stemmed words ["'", "'s", '.', 'a', 'about', 'abroad', 'addit', 'am', 'anyon', 'apply', 'ar', 'assocy', 'at', 'avail', 'ba', 'bba', 'bdesign', 'beyond', 'blu', 'breakfast', 'bsc', 'btech', 'bye', 'caf', 'can', 'cas', 'coff', 'contact', 'cost', 'cours', 'criter', 'cup', 'dat', 'day', 'deadlin', 'degr', 'detail', 'din', 'do', 'doct', 'doe', 'eat', 'elig', 'els', 'emb', 'emerg', 'entail', 'exchang', 'expens', 'facul', 'for', 'get', 'giv', 'good', 'goodby', 'hello', 'help', 'hi', 'hono', 'hospit', 'hour

In [9]:
print("Creating the Data for our Model.....")
training = []
output = []
print("Creating an List (Empty) for Output.....")
output_empty = [0] * len(classes)

print("Creating Training Set, Bag of Words for our Model....")
for doc in documents:
    # Initialize our bag of words
    bag = []
    # List of tokenized words for the pattern
    pattern_words = doc[0]
    # Stem each word
    pattern_words = [stemmer.stem(word.lower()) for word in pattern_words]
 
    # Create our bag of words array
    for w in words:
        bag.append(1) if w in pattern_words else bag.append(0)

    # Output is a '0' for each tag and '1' for current tag
    output_row = list(output_empty)
    output_row[classes.index(doc[1])] = 1

    # Append the feature vector and output row as a tuple
    training.append((bag, output_row))

print("Shuffling Randomly and Converting into Numpy Array for Faster Processing......")
random.shuffle(training)

# Separate feature vectors and output rows into separate lists
train_x = np.array([x[0] for x in training])
train_y = np.array([x[1] for x in training])

print("Creating Train and Test Lists.....")

print("Building Neural Network for Our Chatbot to be Contextual....")
print("Resetting graph data....")
tf.reset_default_graph()


Creating the Data for our Model.....
Creating an List (Empty) for Output.....
Creating Training Set, Bag of Words for our Model....
Shuffling Randomly and Converting into Numpy Array for Faster Processing......
Creating Train and Test Lists.....
Building Neural Network for Our Chatbot to be Contextual....
Resetting graph data....


In [10]:
net = tflearn.input_data(shape=[None, len(train_x[0])])
net = tflearn.fully_connected(net, 8)
net = tflearn.fully_connected(net, 8)
net = tflearn.fully_connected(net, len(train_y[0]), activation='softmax')
net = tflearn.regression(net)
print("Training....")

Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor

Training....


In [11]:
model = tflearn.DNN(net, tensorboard_dir='tflearn_logs')

In [12]:
print("Training the Model.......")
model.fit(train_x, train_y, n_epoch=1000, batch_size=8, show_metric=True)
print("Saving the Model.......")
model.save('model.tflearn')


Training Step: 12999  | total loss: 0.00966 | time: 0.050s
| Adam | epoch: 1000 | loss: 0.00966 - acc: 0.9996 -- iter: 96/98
Training Step: 13000  | total loss: 0.00887 | time: 0.054s
| Adam | epoch: 1000 | loss: 0.00887 - acc: 0.9997 -- iter: 98/98
--
Saving the Model.......
INFO:tensorflow:C:\Users\meghn\model.tflearn is not in all_model_checkpoint_paths. Manually adding it.


In [13]:
print("Pickle is also Saved..........")
#pickling 
pickle.dump( {'words':words, 'classes':classes, 'train_x':train_x, 'train_y':train_y}, open( "training_data", "wb" ) )

Pickle is also Saved..........


In [14]:
print("Loading Pickle.....")
data = pickle.load( open( "training_data", "rb" ) )#serializes the dta (convert in byte stream)
words = data['words']
classes = data['classes']
train_x = data['train_x']
train_y = data['train_y']


with open('intents.json') as json_data:
    intents = json.load(json_data)
    
print("Loading the Model......")
# load our saved model
model.load('./model.tflearn')

Loading Pickle.....
Loading the Model......
INFO:tensorflow:Restoring parameters from C:\Users\meghn\model.tflearn


In [30]:
def clean_up_sentence(sentence):
    # It Tokenize or Break it into the constituents parts of Sentense.
    sentence_words = nltk.word_tokenize(sentence)
    # Stemming means to find the root of the word.
    sentence_words = [stemmer.stem(word.lower()) for word in sentence_words]
    return sentence_words

# Return the Array of Bag of Words: True or False and 0 or 1 for each word of bag that exists in the Sentence
def bow(sentence, words, show_details=False):
    sentence_words = clean_up_sentence(sentence)
    bag = [0]*len(words)
    for s in sentence_words:
        for i,w in enumerate(words):
            if w == s:
                bag[i] = 1
                if show_details:
                    print ("found in bag: %s" % w)
    return(np.array(bag))

ERROR_THRESHOLD = 0.25
print("ERROR_THRESHOLD = 0.25")

def classify(sentence):
    # Prediction or To Get the Posibility or Probability from the Model
    results = model.predict([bow(sentence, words)])[0]
    # Exclude those results which are Below Threshold
    results = [[i,r] for i,r in enumerate(results) if r>ERROR_THRESHOLD]
    # Sorting is Done because heigher Confidence Answer comes first.
    results.sort(key=lambda x: x[1], reverse=True)
    return_list = []
    for r in results:
        return_list.append((classes[r[0]], r[1])) #Tuppl -> Intent and Probability
    return return_list

def response(sentence, userID='123', show_details=False):
    results = classify(sentence)
    if results:
        while results:
            for i in intents['intents']:
                if i['tag'] == results[0][0]:
                    # Return a random response from the list of responses for the matching intent
                    return random.choice(i['responses'])
            results.pop(0)
    # If no matching intent was found, return a default response
    return "Sorry, I didn't understand that."


ERROR_THRESHOLD = 0.25


In [31]:
import gradio as gr

def chat_response(message):
    return response(message)  # Return the response from the chatbot

gr.Interface(fn=chat_response, inputs="text", outputs="text").launch()


Running on local URL:  http://127.0.0.1:7871

To create a public link, set `share=True` in `launch()`.
